# **Instruction Fine-tuning** of Alpaca 🦙 on Arabic
link to **Alpaca Native** Repository -> https://github.com/tatsu-lab/stanford_alpaca

In [ ]:
#Preparing the environement
!pip install -q datasets
!pip install -q loralib
!pip install -q sentencepiece
!pip install -q git+https://github.com/huggingface/transformers.git
# transformers from source
!pip install git+https://github.com/huggingface/transformers -q
!pip install -q accelerate
!pip install -q bitsandbytes
!pip install -q git+https://github.com/huggingface/peft.git

## Importing and Pre-processing the Dataset from 🦙's github repo
> https://github.com/tatsu-lab/stanford_alpaca/blob/main/alpaca_data.json

In [ ]:
!wget https://raw.githubusercontent.com/tatsu-lab/stanford_alpaca/main/alpaca_data.json

--2023-03-18 20:10:45--  https://raw.githubusercontent.com/tatsu-lab/stanford_alpaca/main/alpaca_data.json
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 22773992 (22M) [text/plain]
Saving to: ‘alpaca_data.json’

alpaca_data.json    100%[===================>]  21.72M  --.-KB/s    in 0.1s    

2023-03-18 20:10:47 (192 MB/s) - ‘alpaca_data.json’ saved [22773992/22773992]



> Translation task on the dataset using **GoogleTrans** package

In [ ]:
from datasets import load_dataset
import pandas as pd
import numpy as np

In [ ]:
data = load_dataset("json", data_files="/content/alpaca_data.json")

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
!pip install -q googletrans==3.1.0a0

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for googletrans: filename=googletrans-3.1.0a0-py3-none-any.whl size=16368 sha256=f0ad04a622f36020a3dd8bc89f67bad753c5a77249776687ad2442605107dcf4
  Stored in directory: /root/.cache/pip/wheels/ae/e1/6c/5137bc3f35aa130deea71575e165cc4f4f0680a88f3d90a636
Successfully built googletrans
  Attempting uninstall: googletrans
    Found existing installation: googletrans 3.0.0
    Uninstalling googletrans-3.0.0:
      Successfully uninstalled googletrans-3.0.0


In [ ]:
from googletrans import Translator

> Little sample output

In [ ]:
translator = Translator()
translations = translator.translate(['the lazy dog'],dest='ko')
for translation in translations:
  print(translation.origin, ' -> ', translation.text)

the lazy dog  ->  게으른 개


In [ ]:
def translate_doc(example):
  texts = example['input'] + example['instruction'] + example['output']
  print(texts)
  return {"input":[e.text for e in translator.translate(example['input'], dest='ar',)],
          "instruction":[e.text for e in translator.translate(example['instruction'], dest='ar',)],
          "output":[e.text for e in translator.translate(example['output'], dest='ar',)]}

In [ ]:
# pandas load 3 xlsx files
df1 = pd.read_excel("alpaca_data1.xlsx")
df2 = pd.read_excel("alpaca_data2.xlsx")
df3 = pd.read_excel("alpaca_data3.xlsx")

# concat 3 xlsx files
df = pd.concat([df1, df2, df3])

In [ ]:
df

Unnamed: 0                                            تعليمات  \
0               0                   أعط ثلاث نصائح للبقاء بصحة جيدة.   
1               1                    ما هي الألوان الثلاثة الأساسية؟   
2               2                                     صف بنية الذرة.   
3               3                      كيف يمكننا تقليل تلوث الهواء؟   
4               4              صف وقتًا كان عليك فيه اتخاذ قرار صعب.   
...           ...                                                ...   
17329       51997   قم بإنشاء مثال لما يجب أن ترغب فيه السيرة الذ...   
17330       51998  رتب العناصر الواردة أدناه بالترتيب لإكمال الجم...   
17331       51999                    اكتب فقرة تمهيدية عن شخص مشهور.   
17332       52000   قم بإنشاء قائمة من خمسة أشياء يجب على المرء أ...   
17333       52001   قم بتحليل الوثيقة القانونية المقدمة واشرح الن...   

                                                    مدخل  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
17329                                                NaN   
17330                                      كعكة لي الأكل   
17331                                       ميشيل أوباما   
17332                                                NaN   
17333   ما يلي مقتطف من عقد بين طرفين ، بعنوان "الشرك...   

                                                   انتاج  
0       1- تناول نظامًا غذائيًا متوازنًا وتأكد من تنا...  
1       الألوان الثلاثة الأساسية هي الأحمر والأزرق وا...  
2       تتكون الذرة من نواة تحتوي على البروتونات والن...  
3      هناك عدد من الطرق للحد من تلوث الهواء ، مثل ال...  
4      كان علي أن أتخذ قرارًا صعبًا عندما كنت أعمل كم...  
...                                                  ...  
17329  جين تريمين \ n1234 Main Street، Anytown، CA 98...  
17330                                    أنا آكل الكعكة.  
17331   ميشيل أوباما امرأة ملهمة ارتقت إلى مستوى التح...  
17332  1. ابحث عن الفرص المحتملة وفكر مليًا في الخيار...  
17333  تنص هذه الوثيقة القانونية على أن الشركة "أ" وا...  

[52002 rows x 4 columns]

In [ ]:
import numpy as np

In [ ]:
df.drop(["Unnamed: 0"],axis =1,inplace=True)
df = df.replace(np.nan,'')

In [ ]:
df

تعليمات  \
0                       أعط ثلاث نصائح للبقاء بصحة جيدة.   
1                        ما هي الألوان الثلاثة الأساسية؟   
2                                         صف بنية الذرة.   
3                          كيف يمكننا تقليل تلوث الهواء؟   
4                  صف وقتًا كان عليك فيه اتخاذ قرار صعب.   
...                                                  ...   
17329   قم بإنشاء مثال لما يجب أن ترغب فيه السيرة الذ...   
17330  رتب العناصر الواردة أدناه بالترتيب لإكمال الجم...   
17331                    اكتب فقرة تمهيدية عن شخص مشهور.   
17332   قم بإنشاء قائمة من خمسة أشياء يجب على المرء أ...   
17333   قم بتحليل الوثيقة القانونية المقدمة واشرح الن...   

                                                    مدخل  \
0                                                          
1                                                          
2                                                          
3                                                          
4                                                          
...                                                  ...   
17329                                                      
17330                                      كعكة لي الأكل   
17331                                       ميشيل أوباما   
17332                                                      
17333   ما يلي مقتطف من عقد بين طرفين ، بعنوان "الشرك...   

                                                   انتاج  
0       1- تناول نظامًا غذائيًا متوازنًا وتأكد من تنا...  
1       الألوان الثلاثة الأساسية هي الأحمر والأزرق وا...  
2       تتكون الذرة من نواة تحتوي على البروتونات والن...  
3      هناك عدد من الطرق للحد من تلوث الهواء ، مثل ال...  
4      كان علي أن أتخذ قرارًا صعبًا عندما كنت أعمل كم...  
...                                                  ...  
17329  جين تريمين \ n1234 Main Street، Anytown، CA 98...  
17330                                    أنا آكل الكعكة.  
17331   ميشيل أوباما امرأة ملهمة ارتقت إلى مستوى التح...  
17332  1. ابحث عن الفرص المحتملة وفكر مليًا في الخيار...  
17333  تنص هذه الوثيقة القانونية على أن الشركة "أ" وا...  

[52002 rows x 3 columns]

In [ ]:
from datasets import Dataset, load_dataset
# dataset = Dataset.from_pandas(df)

In [ ]:
dataset = dataset.rename_column(" انتاج",'output')
dataset = dataset.rename_column(" مدخل",'input')
dataset = dataset.rename_column("تعليمات",'instruction') 

In [ ]:
dataset = dataset.remove_columns('__index_level_0__')

In [ ]:
dataset[0]

{'instruction': ' أعط ثلاث نصائح للبقاء بصحة جيدة.',
 'input': '',
 'output': ' 1- تناول نظامًا غذائيًا متوازنًا وتأكد من تناول الكثير من الفواكه والخضروات. \\ n2. تمرن بانتظام لتحافظ على جسمك نشيطًا وقويًا. \\ n3. احصل على قسط كافٍ من النوم وحافظ على جدول نوم ثابت.'}

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


> Saving a checkpoint to upload the dataset from 🤗

In [ ]:
# dataset.push_to_hub("Yasbok/Alpaca_arabic_instruct")

## Fine-tune 🦙 Model using PEFT on instruction fine tuning

> Download the instruction dataset from 🤗 Datasets

In [ ]:
from datasets import Dataset, load_dataset
# dataset = Dataset.from_pandas(df)

In [ ]:
dataset = load_dataset("Yasbok/Alpaca_arabic_instruct")

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
from peft import prepare_model_for_int8_training, LoraConfig, get_peft_model
import bitsandbytes as bnb
from transformers import LlamaTokenizer, LlamaForCausalLM, GenerationConfig


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching /usr/local/cuda/lib64...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.9/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /usr/lib64-nvidia did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('--listen_host=172.28.0.12 --target_host=172.28.0.12 --tunnel_background_save_url=https'), PosixPath('//colab.research.google.com/tun/m/cc48301118ce562b961b3c22d803539adc1e0c19/gpu-t4-s-sejfvmwo7e58 --tunnel_background_save_delay=10s --tunnel_periodic_background_save_frequency=30m0s --enable_output_coalescing=true --output_coalescing_required=t

> Setup 🦙 Pre-trained Model and tokenizer

In [ ]:
MICRO_BATCH_SIZE = 2  # this could actually be 5 but i like powers of 2
BATCH_SIZE = 128
GRADIENT_ACCUMULATION_STEPS = BATCH_SIZE // MICRO_BATCH_SIZE
EPOCHS = 1  # we don't need 3 tbh
LEARNING_RATE = 3e-4  # the Karpathy constant
CUTOFF_LEN = 256  # 256 accounts for about 96% of the data
LORA_R = 8
LORA_ALPHA = 16
LORA_DROPOUT = 0.05

In [ ]:
model = LlamaForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
)
tokenizer = LlamaTokenizer.from_pretrained(
    "decapoda-research/llama-7b-hf", add_eos_token=True
)

model = prepare_model_for_int8_training(model)

config = LoraConfig(
    r=LORA_R,
    lora_alpha=LORA_ALPHA,
    target_modules=["q_proj", "v_proj"],
    lora_dropout=LORA_DROPOUT,
    bias="none",
    task_type="CAUSAL_LM",
) 
tokenizer.pad_token_id = 0
model = get_peft_model(model, config)

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'LLaMATokenizer'. 
The class this function is called from is 'LlamaTokenizer'.


> Template to be used for the instruction fine tuning 🦙 model

In [ ]:
def generate_prompt(data_point):
    # desculpe o desastre de formatação, preciso ser rápido
    if data_point["input"]:
        return f"""يوجد أدناه تعليمات تصف مهمة ، إلى جانب إدخال يوفر المزيد من السياق. اكتب ردًا يكمل الطلب بشكل مناسب.
### تعليمات:
{data_point["instruction"]}
### مدخل:
{data_point["input"]}
### انتاج:
{data_point["output"]}"""
    else:
        return f"""يوجد أدناه تعليمات تصف مهمة. اكتب ردًا يكمل الطلب بشكل مناسب.
### تعليمات:
{data_point["instruction"]}
### انتاج:
{data_point["output"]}"""



def tokenize(prompt):
    # there's probably a way to do this with the tokenizer settings
    # but again, gotta move fast
    result = tokenizer(
        prompt,
        truncation=True,
        max_length=CUTOFF_LEN + 1,
        padding="max_length",
    )
    return {
        "input_ids": result["input_ids"][:-1],
        "attention_mask": result["attention_mask"][:-1],
    }

In [ ]:
dataset = dataset.shuffle().map(lambda x: tokenize(generate_prompt(x)))

Map:   0%|          | 0/52002 [00:00<?, ? examples/s]

In [ ]:
import transformers

> Training the 🦙 model using instruct fine-tuning

In [ ]:
trainer = transformers.Trainer(
    model=model,
    train_dataset=dataset['train'],
    args=transformers.TrainingArguments(
        per_device_train_batch_size=MICRO_BATCH_SIZE,
        gradient_accumulation_steps=GRADIENT_ACCUMULATION_STEPS,
        warmup_steps=100,
        num_train_epochs=EPOCHS,
        learning_rate=LEARNING_RATE,
        fp16=True,
        logging_steps=20,
        output_dir="lora-alpaca",
        save_total_limit=3,
    ),
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)
model.config.use_cache = False
trainer.train(resume_from_checkpoint=False)

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:391: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


KeyboardInterrupt: ignored

> Let's have an insight of our fine tuned Alpaca using Peft

In [ ]:
model

In [ ]:
model.save_pretrained("lora-alpaca_ar")

> Push the adapter to🤗

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [ ]:
model.push_to_hub("Yasbok/Alpaca_instruction_fine_tune_Arabic", use_auth_token=True)

adapter_model.bin:   0%|          | 0.00/16.8M [00:00<?, ?B/s]

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

CommitInfo(commit_url='https://huggingface.co/Yasbok/Alpaca_instruction_fine_tune_Arabic/commit/3aba0407d9ce3306ab400ae7454fc2af52bd8df3', commit_message='Upload model', commit_description='', oid='3aba0407d9ce3306ab400ae7454fc2af52bd8df3', pr_url=None, pr_revision=None, pr_num=None)

## Load you Model from 🤗 and put it to the test

In [ ]:
import torch
import bitsandbytes as bnb
from peft import PeftModel, PeftConfig, prepare_model_for_int8_training, LoraConfig, get_peft_model
from transformers import LlamaTokenizer, LlamaForCausalLM, GenerationConfig

peft_model_id = "Yasbok/Alpaca_instruction_fine_tune_Arabic"
# config = PeftConfig.from_pretrained(peft_model_id)

tokenizer = LlamaTokenizer.from_pretrained("decapoda-research/llama-7b-hf")
model = LlamaForCausalLM.from_pretrained("decapoda-research/llama-7b-hf",
                                          load_in_8bit=True,
                                          device_map="auto",)
# Load the Lora model
model = PeftModel.from_pretrained(model, peft_model_id)


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues


/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /usr/lib64-nvidia did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('--listen_host=172.28.0.12 --target_host=172.28.0.12 --tunnel_background_save_url=https'), PosixPath('//colab.research.google.com/tun/m/cc48301118ce562b961b3c22d803539adc1e0c19/gpu-t4-s-sejfvmwo7e58 --tunnel_background_save_delay=10s --tunnel_periodic_background_save_frequency=30m0s --enable_output_coalescing=true --output_coalescing_required=t

CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching /usr/local/cuda/lib64...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.9/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'LLaMATokenizer'. 
The class this function is called from is 'LlamaTokenizer'.
Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

In [ ]:
def generate_prompt(instruction, input=None):
    if input:
        return f"""يوجد أدناه تعليمات تصف مهمة ، إلى جانب إدخال يوفر المزيد من السياق. اكتب ردًا يكمل الطلب بشكل مناسب.


### تعليمات:
{instruction}

### مدخل:
{input}

### انتاج:"""
    else:
        return f"""يوجد أدناه إرشادات تصف مهمة. يُرجى كتابة رد يكمل الطلب بشكل مناسب.



### تعليمات:
{instruction}

### انتاج:"""

In [ ]:
generation_config = GenerationConfig(
    temperature=0.2,
    top_p=0.75,
    num_beams=4,
)

def evaluate(instruction, input=None):
    prompt = generate_prompt(instruction, input)
    inputs = tokenizer(prompt, return_tensors="pt")
    input_ids = inputs["input_ids"].cuda()
    generation_output = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
        max_new_tokens=256
    )
    for s in generation_output.sequences:
        output = tokenizer.decode(s)
        print("انتاج:", output.split("### انتاج:")[1].strip())

In [ ]:
evaluate(input("تعليمات: "))

تعليمات: أعط ثلاث نصائح للبقاء بصحة جيدة:
انتاج: 1. يجب أن يكون كل يوم للصيام والتخلص من المواد الغذائية. \ n 2. يجب أن يكون كل يوم للصيام والتخلص من المواد الغذائية. \ n 3. يجب أن يكون كل يوم للصيام والتخلص من المواد الغذائية.
